In [1]:
import yfinance as yf
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go

In [2]:
# Get the data from walmart and monster with inteval of 30 minutes

walmart = yf.Ticker("WMT")
monster = yf.Ticker("MNST")

walmart_data = walmart.history(period="60d", interval="2m")
monster_data = monster.history(period="60d", interval="2m")

In [3]:
# plot both tickers on go figure

fig = go.Figure()
fig.add_trace(go.Scatter(x=walmart_data.index, y=walmart_data['Close'], name='walmart'))
fig.add_trace(go.Scatter(x=monster_data.index, y=monster_data['Close'], name='monster'))

fig.show()

In [4]:
print(walmart_data)

                                Open       High        Low      Close  \
Datetime                                                                
2024-03-15 09:30:00-04:00  60.680000  61.110001  60.560001  60.950001   
2024-03-15 09:32:00-04:00  60.950001  61.035000  60.919998  60.990002   
2024-03-15 09:34:00-04:00  60.999901  61.000000  60.840000  60.895302   
2024-03-15 09:36:00-04:00  60.880001  60.919998  60.790001  60.910000   
2024-03-15 09:38:00-04:00  60.910000  60.959999  60.868999  60.910000   
...                              ...        ...        ...        ...   
2024-04-26 15:50:00-04:00  60.169998  60.169998  60.110001  60.115002   
2024-04-26 15:52:00-04:00  60.110001  60.160000  60.099998  60.137402   
2024-04-26 15:54:00-04:00  60.139999  60.149899  60.084999  60.110001   
2024-04-26 15:56:00-04:00  60.110001  60.139999  60.099998  60.122501   
2024-04-26 15:58:00-04:00  60.123001  60.189999  60.119999  60.130001   

                            Volume  Dividends  Sto

In [5]:
# plot eith candle stick

fig = go.Figure(data=[go.Candlestick(x=walmart_data.index,
                open=walmart_data['Open'],
                high=walmart_data['High'],
                low=walmart_data['Low'],
                close=walmart_data['Close'])])

# plot moving average of 20 ticks and 80 ticks

fig.add_trace(go.Scatter(x=walmart_data.index, y=walmart_data['Close'].rolling(window=5).mean(), name='5 Ticks MA'))
fig.add_trace(go.Scatter(x=walmart_data.index, y=walmart_data['Close'].rolling(window=20).mean(), name='20 Ticks MA'))

fig.show()

In [6]:
# count the number of times the 5 ticks MA crosses the 20 ticks MA

walmart_data['5T_MA'] = walmart_data['Close'].rolling(window=5).mean()
walmart_data['20T_MA'] = walmart_data['Close'].rolling(window=20).mean()

walmart_data['signal'] = np.where(walmart_data['5T_MA'] > walmart_data['20T_MA'], 1, 0)
walmart_data['signal'] = walmart_data['signal'].diff()

print(walmart_data['signal'].value_counts())

# plot the buy and sell signals

fig = go.Figure(data=[go.Candlestick(x=walmart_data.index,
                open=walmart_data['Open'],
                high=walmart_data['High'],
                low=walmart_data['Low'],
                close=walmart_data['Close'])])

fig.add_trace(go.Scatter(x=walmart_data.index, y=walmart_data['Close'].rolling(window=5).mean(), name='5 Ticks MA'))
fig.add_trace(go.Scatter(x=walmart_data.index, y=walmart_data['Close'].rolling(window=20).mean(), name='20 Ticks MA'))

buy_signals = walmart_data[walmart_data['signal'] == 1]
sell_signals = walmart_data[walmart_data['signal'] == -1]

fig.add_trace(go.Scatter(x=buy_signals.index, y=buy_signals['Close'], mode='markers', marker=dict(color='green', size=10), name='Buy Signal'))

fig.add_trace(go.Scatter(x=sell_signals.index, y=sell_signals['Close'], mode='markers', marker=dict(color='red', size=10), name='Sell Signal'))

fig.show()

signal
 0.0    5463
 1.0     192
-1.0     192
Name: count, dtype: int64


In [7]:
# calculate profit and loss

walmart_data['buy_price'] = np.where(walmart_data['signal'] == 1, walmart_data['Close'], np.nan)
walmart_data['sell_price'] = np.where(walmart_data['signal'] == -1, walmart_data['Close'], np.nan)

walmart_data['buy_price'] = walmart_data['buy_price'].ffill()
walmart_data['sell_price'] = walmart_data['sell_price'].ffill()

walmart_data['PnL'] = walmart_data['sell_price'] - walmart_data['buy_price']

print(walmart_data['PnL'].sum())

# plot the profit and loss

fig = go.Figure(data=[go.Candlestick(x=walmart_data.index,
                open=walmart_data['Open'],
                high=walmart_data['High'],
                low=walmart_data['Low'],
                close=walmart_data['Close'])])

fig.add_trace(go.Scatter(x=walmart_data.index, y=walmart_data['Close'].rolling(window=5).mean(), name='5 Ticks MA'))
fig.add_trace(go.Scatter(x=walmart_data.index, y=walmart_data['Close'].rolling(window=20).mean(), name='20 Ticks MA'))

buy_signals = walmart_data[walmart_data['signal'] == 1]
sell_signals = walmart_data[walmart_data['signal'] == -1]

fig.add_trace(go.Scatter(x=buy_signals.index, y=buy_signals['Close'], mode='markers', marker=dict(color='green', size=10), name='Buy Signal'))
fig.add_trace(go.Scatter(x=sell_signals.index, y=sell_signals['Close'], mode='markers', marker=dict(color='red', size=10), name='Sell Signal'))

fig.show()

-153.24288177490234


In [8]:
ratio_0 = (walmart_data['Close'].iloc[0]) / (monster_data['Close'].iloc[0])
ratio_0

1.012458471602906

In [9]:
monster_data['Close_NORM'] = monster_data['Close'].multiply(ratio_0).round(6)

In [10]:
walmart_monster_dif = walmart_data['Close'] - monster_data['Close_NORM']
walmart_monster_dif

Datetime
2024-03-15 09:30:00-04:00   -2.370605e-07
2024-03-15 09:32:00-04:00    8.050068e-02
2024-03-15 09:34:00-04:00    1.617282e-02
2024-03-15 09:36:00-04:00    1.321188e-01
2024-03-15 09:38:00-04:00    9.161985e-02
                                 ...     
2024-04-26 15:50:00-04:00    6.085154e+00
2024-04-26 15:52:00-04:00    6.112617e+00
2024-04-26 15:54:00-04:00    6.075093e+00
2024-04-26 15:56:00-04:00    6.087593e+00
2024-04-26 15:58:00-04:00    6.145716e+00
Length: 5850, dtype: float64

In [11]:
# Plot the difference between the two tickers

fig = go.Figure()
fig.add_trace(go.Scatter(x=walmart_monster_dif.index, y=walmart_monster_dif, name='walmart-monster'))

fig.show()

In [12]:
# Plot the two normalized tickers

fig = go.Figure()
fig.add_trace(go.Scatter(x=walmart_data.index, y=walmart_data['Close'], name='walmart'))
fig.add_trace(go.Scatter(x=monster_data.index, y=monster_data['Close_NORM'], name='monster'))

fig.show()

In [14]:
# Plot the difference and its moving average

fig = go.Figure()
fig.add_trace(go.Scatter(x=walmart_monster_dif.index, y=walmart_monster_dif, name='walmart-monster'))
fig.add_trace(go.Scatter(x=walmart_monster_dif.index, y=walmart_monster_dif.rolling(window=5).mean(), name='5 Ticks MA'))
fig.add_trace(go.Scatter(x=walmart_monster_dif.index, y=walmart_monster_dif.rolling(window=20).mean(), name='20 Ticks MA'))

fig.show()


In [15]:
walmart_monster_dif = walmart_monster_dif.to_frame()
walmart_monster_dif.columns = ['Close']

In [16]:
walmart_monster_dif['10T_MA'] = walmart_monster_dif['Close'].rolling(window=10).mean()
walmart_monster_dif['60T_MA'] = walmart_monster_dif['Close'].rolling(window=60).mean()

walmart_monster_dif['signal'] = np.where(walmart_monster_dif['10T_MA'] > walmart_monster_dif['60T_MA'], 1, 0)
walmart_monster_dif['signal'] = walmart_monster_dif['signal'].diff()

print(walmart_monster_dif['signal'].value_counts())

# Plot the signals

fig = go.Figure()
fig.add_trace(go.Scatter(x=walmart_monster_dif.index, y=walmart_monster_dif['Close'], name='walmart-monster'))
fig.add_trace(go.Scatter(x=walmart_monster_dif.index, y=walmart_monster_dif.rolling(window=10).mean()['Close'], name='10 Ticks MA'))
fig.add_trace(go.Scatter(x=walmart_monster_dif.index, y=walmart_monster_dif.rolling(window=50).mean()['Close'], name='60 Ticks MA'))

buy_signals = walmart_monster_dif[walmart_monster_dif['signal'] == 1]
sell_signals = walmart_monster_dif[walmart_monster_dif['signal'] == -1]

fig.add_trace(go.Scatter(x=buy_signals.index, y=buy_signals['Close'], mode='markers', marker=dict(color='green', size=10), name='Buy Signal'))
fig.add_trace(go.Scatter(x=sell_signals.index, y=sell_signals['Close'], mode='markers', marker=dict(color='red', size=10), name='Sell Signal'))

fig.show()


signal
 0.0    5703
 1.0      73
-1.0      73
Name: count, dtype: int64


In [17]:
#Consider walmart as the first and monster as the second ticker.
#When there is a buy signal for walmart, we buy walmart and sell monster.
#When there is a sell signal for walmart, we sell walmart and buy monster.

In [18]:
#Copy signal column from difference dataframe to walmart dataframe
walmart_data['signal'] = walmart_monster_dif['signal']
monster_data['signal'] = -walmart_monster_dif['signal']